In [1]:
import pandas as pd

In [2]:
# read the csv file
data = pd.read_csv('inputs/train.csv', index_col='id')
data['date'] = pd.to_datetime(data['date'])

/home/arlamb/.local/lib/python3.8/site-packages/numpy/lib/arraysetops.py:580: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  mask |= (ar1 == a)


In [3]:
# combine store and item column as time_series
data['store'] = ['store_' + str(i) for i in data['store_nbr']]
data['family'] = ['item_' + str(i) for i in data['family']]
data['time_series'] = data[['store', 'family']].apply(lambda x: '_'.join(x), axis=1)
print(f"Number of stores: {data['store_nbr'].nunique()}")
print(f"Number of product families: {data['family'].nunique()}")
data.drop(['store', 'family', 'store_nbr'], axis=1, inplace=True)

Number of stores: 54
Number of product families: 33


In [4]:
# extract features from date
data['month'] = [i.month for i in data['date']]
data['year'] = [i.year for i in data['date']]
data['day_of_week'] = [i.dayofweek for i in data['date']]
data['day_of_year'] = [i.dayofyear for i in data['date']]

In [5]:
data.head()

date  sales  onpromotion              time_series  month  year  \
id                                                                        
0  2013-01-01    0.0            0  store_1_item_AUTOMOTIVE      1  2013   
1  2013-01-01    0.0            0   store_1_item_BABY CARE      1  2013   
2  2013-01-01    0.0            0      store_1_item_BEAUTY      1  2013   
3  2013-01-01    0.0            0   store_1_item_BEVERAGES      1  2013   
4  2013-01-01    0.0            0       store_1_item_BOOKS      1  2013   

    day_of_week  day_of_year  
id                            
0             1            1  
1             1            1  
2             1            1  
3             1            1  
4             1            1

In [6]:
data['time_series'].nunique()

1782

In [7]:
# import plotly.express as px
# for i in data['time_series'].unique()[:1]:
#     subset = data[data['time_series'] == i].copy()
#     subset['moving_average'] = subset['sales'].rolling(30).mean()
#     fig = px.line(subset, x="date", y=["sales","moving_average"], title = i, template = 'plotly_dark')
#     fig.show()

In [8]:
from tqdm import tqdm
from pycaret.regression import *

all_ts = data['time_series'].unique()

all_results = []
final_model = {}

for i in tqdm(all_ts):
    
    df_subset = data[data['time_series'] == i]
    
    # initialize setup from pycaret.regression
    s = setup(df_subset, target = 'sales', train_size = 0.95,
              data_split_shuffle = False, fold_strategy = 'timeseries', fold = 3,
              ignore_features = ['date', 'time_series'],
              numeric_features = ['day_of_year', 'year'],
              categorical_features = ['month', 'day_of_week'],
              silent = True, verbose = False, session_id = 123)
    
    # compare all models and select best one based on MAE
    best_model = compare_models(sort = 'MAE', verbose=False)
    
    # capture the compare result grid and store best model in list
    p = pull().iloc[0:1]
    p['time_series'] = str(i)
    all_results.append(p)
    
    # finalize model i.e. fit on entire data including test set
    f = finalize_model(best_model)
    
    # attach final model to a dictionary
    final_model[i] = f
    
    # save transformation pipeline and model as pickle file 
    if '/' in i: i = i.replace('/', '_')
    save_model(f, model_name='trained_models/' + str(i), verbose=False)

  0%|          | 0/1782 [00:00<?, ?it/s]/home/arlamb/anaconda3-2021/envs/cs567-3.8/lib/python3.8/site-packages/sklearn/utils/deprecation.py:101: FutureWarning: Attribute standard_coef_ was deprecated in version 0.23 and will be removed in 0.25.
  warnings.warn(msg, category=FutureWarning)
/home/arlamb/anaconda3-2021/envs/cs567-3.8/lib/python3.8/site-packages/sklearn/utils/deprecation.py:101: FutureWarning: Attribute standard_intercept_ was deprecated in version 0.23 and will be removed in 0.25.
  warnings.warn(msg, category=FutureWarning)
/home/arlamb/anaconda3-2021/envs/cs567-3.8/lib/python3.8/site-packages/sklearn/utils/deprecation.py:101: FutureWarning: Attribute average_coef_ was deprecated in version 0.23 and will be removed in 0.25.
  warnings.warn(msg, category=FutureWarning)
/home/arlamb/anaconda3-2021/envs/cs567-3.8/lib/python3.8/site-packages/sklearn/utils/deprecation.py:101: FutureWarning: Attribute average_intercept_ was deprecated in version 0.23 and will be removed in 0.2